# Source code to generate Monte-Carlo simulations data

In [10]:
import numpy as np, random as rd
import itertools, os, matplotlib.pyplot as mb
mb.rcParams['text.usetex'] = True

In [5]:
def fixcompdB(fp,f,N): #dB Fixation probability of a mutant with fitness fp on complete graph of size N in a bakground fitness f.
    phi=0
    if(fp != f):
        phi=((N-1)/N)*(1-(f/fp))/(1-(f/fp)**(N-1))  
    else:
        phi=1/N    
    return phi;

def fixstarunidB(fp,f,N): #Uniform initialised dB fixation probability of a mutant with fitness fp on the star graph of size N. 
    if(fp != f):
        num= ((N-1)/N)+((N-1)*(fp/f))/(N-2+2*(fp/f))
        den= N*(1+(N-2)/(1+(N-1)*(fp/f)))
        phi=num/den
    else:
        phi=2*(N-1)/((N**2)*(1+((N-2)/N)))
    return phi;


def fixstartempdB(fp,f,N):  #Temperature initialised dB fixation probability of a mutant with fitness fp on the star graph of size N. 
    if(fp != f):
        num= (1+(N-1)*(fp/f))*((((N-1)**2)/N)+((fp/f)/(N-2+2*(fp/f))))
        den= N*(N-1)*(1+(fp/f))
        phi=num/den
    else:
        phi=(((1/N)+(((N-1)**2)/N))/(2*(N-1)))
    return phi;



In [9]:
def fixcompBd(fp,f,N):
    phi=0
    if(fp != f):
        phi=(1-(f/fp))/(1-(f/fp)**N)  
    else:
        phi=1/N    
    return phi

def fixstaruniBd(fp,f,N):  #Uniform initialised Bd fixation probability of a mutant with fitness fp on the star graph of size N. 
    if(fp != f):
        num= (f-fp)*(f+fp)*(f+fp*(N-1)+f*(N-2)*(N-1))
        den= (f+fp*(N-1))*(-fp*(fp+(N-1)*f)+f*(f+fp*(N-1))*(((f/fp)*(fp+(N-1)*f)/(f+fp*(N-1)))**(N-1)))
        phi=num/den
    else:
        phi=1/N
    return phi;

def fixstartempBd(fp,f,n,x,y):  #Uniform initialised Bd fixation probability of a mutant with fitness fp on the weighted star graph of size N with n leaves. Set x=y=1 for undirected star graph.  
    if(fp != f):
        num=(1-(fp/f)**2)*((n**3)*(1-x)*(x**2)+(n**2)*x*y*((fp/f)+x)+n*x*y*((fp/f)+y)-(y-1)*y**2)
        den=(n+1)*(n*(fp/f)*x+y)*((n*(fp/f)*x+y)*(((n*x+(fp/f)*y)/(n*((fp/f)**2)*x+(fp/f)*y))**n)-(fp/f)*(n*x+(fp/f)*y))
        phi=num/den
    else:
        phi=-((n**2)*(-1 + x)*x -2*n*x*y+(-1 + y)*y)/((1 + n)*((n**2)*x + y))
    return phi;


                     

In [6]:
###Uncomment below only if you want to overwrite the exsiting data. 
# path=os.getcwd()
# subpath1='/Data/Fig_4/dB/average_fitness/'    # Path to the directory where average fitness data for dB updating will be saved.
# subpath2='/Data/Fig_4/dB/standard_deviation/'    # Path to the directory where standard deviation data for dB updating will be saved.
    

In [8]:
# Parameters used here are the same as in the paper. 
#Warning: It might get very slow to work with these parameters. Please change parameters at your convenience. 

Trials=2000  # Number of independent realisations
N=np.arange(5,106,5,dtype='int')      # Population size
Maxmut=int(100)*(N)  # Maximum number of mutations sampled per realisation



networkS=['complete_dB','star_dB_uni','star_dB_temp']

fmin=0.1
fmax=10

for network in networkS:
    fitness_N=np.zeros(np.size(N))
    fitness_N_std=np.zeros(np.size(N))
    for n in range(np.size(N)):
        fitness=np.zeros((Trials,Maxmut[n]))
        fitness[:,0]=1
        for i in range(Trials):
            for j in range(1,Maxmut[n]):
                mut_fitness=rd.uniform(fmin, fmax)
                dice=rd.uniform(0, 1)
                if(network=='complete_dB'):
                    if(dice<fixcompdB(mut_fitness,fitness[i,j-1],N[n])):
                        fitness[i,j]=mut_fitness
                    else:
                        fitness[i,j]=fitness[i,j-1]
                elif(network=='star_dB_uni'):
                    if(dice<fixstarunidB(mut_fitness,fitness[i,j-1],N[n])):
                        fitness[i,j]=mut_fitness
                    else:
                        fitness[i,j]=fitness[i,j-1]       
                elif(network=='star_dB_temp'):
                    if(dice<fixstartempdB(mut_fitness,fitness[i,j-1],N[n])):
                        fitness[i,j]=mut_fitness
                    else:
                        fitness[i,j]=fitness[i,j-1]                
        fitness_av=np.zeros(Maxmut[n])
        for i in range(Maxmut[n]):
            fitness_av[i]=np.sum(fitness[:,i])/Trials
        fitness_N[n]=fitness_av[Maxmut[n]-1] 
        fitness_N_std[n]=np.std(fitness[:,Maxmut[n]-1])
### Uncomment below only if you want to overwrite the existing dB data. 
#     if(network=='complete_dB'):
#         np.save(path+subpath1+'11_complete_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N)
#         np.save(path+subpath2+'11_complete_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N_std)
#     elif(network=='star_dB_uni'):
#         np.save(path+subpath1+'11_star_uni_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N)
#         np.save(path+subpath2+'11_star_uni_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N_std) 
#     elif(network=='star_dB_temp'):
#         np.save(path+subpath1+'11_star_temp_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N)
#         np.save(path+subpath2+'11_star_temp_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N_std)     

In [ ]:
###Uncomment below only if you want to overwrite the exsiting data. 
# path=os.getcwd()
# subpath3='/Data/Fig_4/Bd/average_fitness/'    # Path to the directory where average fitness data for Bd updating will be saved.
# subpath4='/Data/Fig_4/Bd/standard_deviation/'    # Path to the directory where standard deviation data for Bd updating will be saved.


In [ ]:
# Parameters used here are the same as in the paper. 
#Warning: It might get very slow to work with these parameters. Please change parameters at your convenience. 

Trials=2000  # Number of independent realisations
N=np.arange(5,106,5,dtype='int')      # Population size
Maxmut=int(100)*(N)  # Maximum number of mutations sampled per realisation



networkS=['complete_Bd','star_Bd_uni']

fmin=0.1
fmax=10

for network in networkS:
    fitness_N=np.zeros(np.size(N))
    fitness_N_std=np.zeros(np.size(N))
    for n in range(np.size(N)):
        fitness=np.zeros((Trials,Maxmut[n]))
        fitness[:,0]=1
        for i in range(Trials):
            for j in range(1,Maxmut[n]):
                mut_fitness=rd.uniform(fmin, fmax)
                dice=rd.uniform(0, 1)
                if(network=='complete_Bd'):
                    if(dice<fixcompBd(mut_fitness,fitness[i,j-1],N[n])):
                        fitness[i,j]=mut_fitness
                    else:
                        fitness[i,j]=fitness[i,j-1]
                elif(network=='star_Bd_uni'):
                    if(dice<fixstaruniBd(mut_fitness,fitness[i,j-1],N[n])):
                        fitness[i,j]=mut_fitness
                    else:
                        fitness[i,j]=fitness[i,j-1]                      
        fitness_av=np.zeros(Maxmut[n])
        for i in range(Maxmut[n]):
            fitness_av[i]=np.sum(fitness[:,i])/Trials
        fitness_N[n]=fitness_av[Maxmut[n]-1] 
        fitness_N_std[n]=np.std(fitness[:,Maxmut[n]-1])
### Uncomment below only if you want to overwrite the existing dB data. 
#     if(network=='complete_Bd'):
#         np.save(path+subpath3+'isothermal_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N)
#         np.save(path+subpath4+'isothermal_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N_std)
#     elif(network=='star_Bd_uni'):
#         np.save(path+subpath3+'star_uni_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N)
#         np.save(path+subpath4+'star_uni_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N_std) 


In [ ]:
# Same code as above. Only change is the order of the maximum number of mutations sampled per realisation for the star graph, a supprsessor of fixation.
# Parameters used here are the same as in the paper. 
#Warning: It will get super slow to work with these parameters. Please change parameters at your convenience.



Trials=2000

N=np.arange(10,110,10,dtype='int')  
Maxmut=100000*N

fmin=0.1
fmax=10


networkS=['star_Bd_temp']

for network in networkS:
    fitness_N=np.zeros(np.size(N))
    fitness_N_std=np.zeros(np.size(N))
    for n in range(np.size(N)):
        fitness=np.zeros((Trials,Maxmut[n]))
        fitness[:,0]=1
        for i in range(Trials):
            for j in range(1,Maxmut[n]):
                mut_fitness=rd.uniform(fmin, fmax)
                dice=rd.uniform(0, 1)
                if(network=='star_Bd_temp'):
                    if(dice<fixstartempBd(mut_fitness,fitness[i,j-1],N[n]-1,1,1)):
                        fitness[i,j]=mut_fitness
                    else:
                        fitness[i,j]=fitness[i,j-1]       
        fitness_av=np.zeros(Maxmut[n])
        for i in range(Maxmut[n]):
            fitness_av[i]=np.sum(fitness[:,i])/Trials
        fitness_N[n]=fitness_av[Maxmut[n]-1] 
        fitness_N_std[n]=np.std(fitness[:,Maxmut[n]-1])
        print(network, N[n])
        ##Uncomment the following line, if you want to overwrite the existing 'Monte-Carlo' data!
#     if(network=='star_dB_temp'):
#         np.save(path+subpath3+'star_temp_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N)
#         np.save(path+subpath4+'star_temp_fmin_{}_fmax_{}_Trials_{}.npy'.format(fmin,fmax,Trials),fitness_N_std)     
        